In [27]:
import pandas as pd
import numpy as np
import scipy as sp
import pickle
import numbers
import DataLoader
from PretrainedEstimator import PretrainedEstimator
from sklearn.model_selection import cross_val_score
from sklearn.linear_model import SGDClassifier, LogisticRegression
from sklearn.ensemble import RandomForestClassifier
from sklearn.feature_extraction import DictVectorizer
from sklearn.feature_selection import RFECV
from sklearn.metrics import f1_score, recall_score, precision_score

In [60]:
# Load the relevant dataset and pass it to DataLoader for preprocessing

# Ratings Only Dataset
ratings = pd.read_csv("data/all_recipe_small_clean.csv")
recipes = None

# Full Recipe Dataset
# ratings = pd.read_csv("data/all_ratings.csv")
# with open("data/all_recipes.pkl", "rb") as infile:
#     recipes = pickle.load(infile) 

dataLoader = DataLoader.DataLoader(ratings, recipes)
user_holdout, recipe_holdout, holdout = dataLoader.get_holdout_data()
holdout_X = [t[:2] for t in holdout]
holdout_Y = np.array([t[2] for t in holdout])

In [45]:
class RecipeMeanEstimator:
    """
    Just guesses the mean for the recipe
    """
    def __init__(self, dataLoader, recipe_holdout):
        self.dataLoader = dataLoader
        self.recipe_holdout = recipe_holdout
        
    def get_recipe_average(self, recipe_id):
        ratings = self.dataLoader.get_recipe_ratings(
            recipe_id, self.recipe_holdout)
        return np.round(np.mean(np.fromiter(ratings.values(), dtype=np.int64)))
    
    def fit(self, X, y):
        """
        X: list of (user_id, recipe_id) tuple
        y: np.array user rating
        """
        return self.predict(X)
    
    def predict(self, X):
        """
        X: list of (user_id, recipe_id) tuple
        """
        return np.array([self.get_recipe_average(recipe_id) for _, recipe_id in X])
    
    def get_params(self, deep=False):
        return {
            'dataLoader': self.dataLoader,
            'recipe_holdout': self.recipe_holdout
        }
        

In [46]:
class UserMeanEstimator:
    """
    Just guesses the user rating mean
    """
    def __init__(self, dataLoader, user_holdout):
        self.dataLoader = dataLoader
        self.user_holdout = user_holdout
        
    def get_user_average(self, user_id):
        ratings = self.dataLoader.get_user_ratings(user_id, self.user_holdout)
        return np.round(np.mean(np.fromiter(ratings.values(), dtype=np.int64)))
        
    def fit(self, X, y):
        """
        X: list of (user_id, recipe_id) tuple
        y: np.array user rating
        """
        return self.predict(X)
    
    def predict(self, X):
        """
        X: list of (user_id, recipe_id) tuple
        """
        return np.array([self.get_user_average(user_id) for user_id, _ in X])
    
    def get_params(self, deep=False):
        return {
            'dataLoader': self.dataLoader,
            'user_holdout': self.user_holdout
        }
            

In [47]:
class TunedMeanEstimator:
    """
    Takes a weighted average of the user's average rating and the
    recipe's average rating, then tunes the weighting parameter w
    based on data.
    """
    def __init__(self, dataLoader, recipe_holdout, user_holdout):
        self.dataLoader = dataLoader
        self.recipe_holdout = recipe_holdout
        self.user_holdout = user_holdout
        self.w = np.array([0.8, 0.2])
        self.eta = 0.01
    def get_recipe_average(self, recipe_id):
        ratings = self.dataLoader.get_recipe_ratings(
            recipe_id, self.recipe_holdout)
        return np.mean(np.fromiter(ratings.values(), dtype=np.int64))
    
    def get_user_average(self, user_id):
        ratings = self.dataLoader.get_user_ratings(user_id, self.user_holdout)
        return np.mean(np.fromiter(ratings.values(), dtype=np.int64))
        
    def fit(self, X, y):
        self.eta = 0.01
        feats = [np.array([self.get_user_average(user_id), self.get_recipe_average(recipe_id)]) for user_id, recipe_id in X]
        for epoch in range(10):
            for i, feat in enumerate(feats):
                pred = np.dot(self.w, feat)
                loss = pred - y[i]
                self.w -= self.eta*2*loss*feat
            self.eta /= 2
        print(self.w)
    
    def predict(self, X):
        feats = [np.array([self.get_user_average(user_id), self.get_recipe_average(recipe_id)]) for user_id, recipe_id in X]
        return [np.round(np.dot(self.w, feat)) for feat in feats]
    
    def get_params(self, deep=False):
        return {
            'dataLoader': self.dataLoader,
            'user_holdout': self.user_holdout,
            'recipe_holdout': self.recipe_holdout,
        }

In [48]:
class SimpleSGDEstimator:
    """
    Performs stochastic gradient descent on key features including recipe
    categories and ingredients.
    """
    def __init__(self, dataLoader, recipe_holdout, user_holdout):
        self.dataLoader = dataLoader
        self.recipe_holdout = recipe_holdout
        self.user_holdout = user_holdout
        self.classifier = SGDClassifier(class_weight='balanced', alpha=0.001)
        self.vec = DictVectorizer()
  
    def get_recipe_average(self, recipe_id):
        ratings = self.dataLoader.get_recipe_ratings(
            recipe_id, self.recipe_holdout)
        return np.mean(np.fromiter(ratings.values(), dtype=np.int64))
    
    def get_user_average(self, user_id):
        ratings = self.dataLoader.get_user_ratings(user_id, self.user_holdout)
        return np.mean(np.fromiter(ratings.values(), dtype=np.int64))
        
    def get_feat_dict(self, user_id, recipe_id):
        user_ratings = self.dataLoader.get_user_ratings(user_id, self.user_holdout)
        avg_user_rating = np.mean(np.fromiter(user_ratings.values(), dtype=np.int64))
        
        recipe_ratings = self.dataLoader.get_recipe_ratings(
            recipe_id, self.recipe_holdout)
        avg_recipe_rating = np.mean(np.fromiter(recipe_ratings.values(), dtype=np.int64))
        recipe_info = self.dataLoader.get_recipe_info(recipe_id)
        
        calories = recipe_info['calories'] if not recipe_info['calories'] is None else 0
        
        feats = {
            'user_id': user_id,
            'recipe_id': recipe_id,
            'avg_user_rating': avg_user_rating,
            'avg_recipe_rating': avg_recipe_rating,
            'calories': calories
        }
        
        for category in recipe_info["categories"]:
            feats["cat_{}".format(category)] = 1
        for ingredient in recipe_info["ingredients"]["full list"]:
            ing_name = ingredient["key ingredient"]
            quantity = ingredient["quantity"]
            feats["ing_{}".format(ing_name)] = quantity if not quantity is None else 1
        
        return feats
        
    def fit(self, X, y):
        feats = [self.get_feat_dict(user_id, recipe_id) for user_id, recipe_id in X]
        feats = self.vec.fit_transform(feats)
        return self.classifier.fit(feats, y)
    
    def predict(self, X):
        feats = [self.get_feat_dict(user_id, recipe_id) for user_id, recipe_id in X]
        feats = self.vec.transform(feats)
        return self.classifier.predict(feats)
    
    def get_params(self, deep=False):
        return {
            'dataLoader': self.dataLoader,
            'user_holdout': self.user_holdout,
            'recipe_holdout': self.recipe_holdout,
        }

In [102]:
class CollaborativeFilteringEstimator:
    """
    Uses item-item collaborative filtering to predict the user rating
    """
    def __init__(self, dataLoader, recipe_holdout, user_holdout, similarity=None, split='train'):
        self.dataLoader = dataLoader
        self.split = split
        self.recipe_holdout = recipe_holdout
        self.user_holdout = user_holdout
        self.index_to_recipe_id = [id for id in self.dataLoader.get_recipe_ids()]
        self.recipe_id_to_index = { id: idx for idx, id in enumerate(self.index_to_recipe_id) }
        if similarity is None:
            self.similarity = self.compute_similarity_matrix()
        else:
            self.similarity = similarity
        
    def compute_similarity_matrix(self):
        
        num_recipes = len(self.recipe_id_to_index)
        sim = np.zeros((num_recipes, num_recipes))
        
        # since symmetric, only have sim[smallerIndex][largerIndex]
        indices = list(enumerate(self.index_to_recipe_id))
        
        for idx1, recipe1 in indices:
            ratings1 = self.dataLoader.get_recipe_ratings(recipe1, self.recipe_holdout, self.split)
            
            related_recipes = set()
            for user_id in dataLoader.get_recipe_ratings(recipe1, recipe_holdout, self.split).keys():
                rated_recipes = dataLoader.get_user_ratings(user_id, user_holdout).keys()
                related_recipes = related_recipes.union(rated_recipes)
            
            for recipe2 in related_recipes:
                idx2 = self.recipe_id_to_index[recipe2]
                if idx2 > idx1:
                    sim[idx1][idx2] = self.compute_cosine_similiarity(ratings1, recipe2)
        return sim
    
    def compute_cosine_similiarity(self, ratings1, r2):
        # TODO: Test
        def zero_center_ratings(ratings):
            rating_mean = sum(ratings.values()) / len(ratings)
            return { rid : value - rating_mean for rid, value in ratings.items() }

        def l2_norm(ratings):
            return np.linalg.norm(np.fromiter(ratings.values(), dtype=np.float64))
  
        
        ratings2 = self.dataLoader.get_recipe_ratings(r2, self.recipe_holdout, self.split)
        
        ratings1 = zero_center_ratings(ratings1)
        ratings2 = zero_center_ratings(ratings2)
        
        norm1 = l2_norm(ratings1)
        norm2 = l2_norm(ratings2)
        
        if norm1 == 0.0 or norm2 == 0.0:
            return 0.0
        
        prod = 0
        for k in ratings1:
            if k in ratings2:
                prod += ratings1[k] * ratings2[k]
        return prod / (norm1 * norm2)

#         ratings2 = self.dataLoader.get_recipe_ratings(r2, self.recipe_holdout, self.split)
#         prod = 0
#         for k in ratings1:
#             if k in ratings2:
#                 prod += ratings1[k] * ratings2[k]
#         return prod / (len(ratings1) * len(ratings2))
        
    def fit(self, X, y):
        """
        X: list of (user_id, recipe_id) tuple
        y: np.array user rating
        """
        return self.predict(X)
    
    def predict(self, X):
        """
        X: list of (user_id, recipe_id) tuple
        """
        preds = []
        for user_id, recipe_id in X:
            user_ratings = self.dataLoader.get_user_ratings(user_id, self.user_holdout)
            user_mean_rating = np.mean(np.fromiter(user_ratings.values(), dtype=np.int64))
            numer = 0.0
            denom = 0.0
            pred_idx = self.recipe_id_to_index[recipe_id]
            for neighbor_rid, rating in user_ratings.items():
                neighbor_idx = self.recipe_id_to_index[neighbor_rid]
                low_id, high_id = tuple(sorted([pred_idx, neighbor_idx]))
                sim = self.similarity[low_id][high_id]
                numer += sim * (rating - user_mean_rating)
                denom += np.abs(sim)
            if denom == 0.0:
                pred = user_mean_rating
            else:
                pred = user_mean_rating + numer / denom
            preds.append(pred)
        return np.clip(np.round(np.array(preds)), 1.0, 5.0)
        
    def get_params(self, deep=False):
        return {
            'dataLoader': self.dataLoader,
            'user_holdout': self.user_holdout,
            'recipe_holdout': self.recipe_holdout,
            'similarity': self.similarity,
        }

In [55]:
class LogisticEstimator:
    """
    Uses logistic regression to train weights for a feature set to predict ratings.
    If features='rich', the feature set includes recipe ingredient and category information.
    Otherwise, features come from ratings of the target recipe and the target user's
    ratings of other recipes.
    """
    def __init__(self, dataLoader, recipe_holdout, user_holdout, features='rich'):
        self.dataLoader = dataLoader
        self.recipe_holdout = recipe_holdout
        self.user_holdout = user_holdout
        self.regressor = LogisticRegression(max_iter=100, penalty='l1', class_weight='balanced')
        self.vec = DictVectorizer()
        self.use_features = features
        
        self.recipe_id_to_index = { id: idx for idx, id in enumerate(dataLoader.get_recipe_ids()) }
    
    def extract_features(self, X):
        feats = [self.get_feature_dict(user_id, recipe_id) for user_id, recipe_id in X]
        return feats
        
    def get_feature_dict(self, user_id, recipe_id):
        user_ratings = self.dataLoader.get_user_ratings(user_id, self.user_holdout)
        avg_user_rating = np.mean(np.fromiter(user_ratings.values(), dtype=np.int64))
        
        recipe_ratings = self.dataLoader.get_recipe_ratings(
            recipe_id, self.recipe_holdout)
        avg_recipe_rating = np.mean(np.fromiter(recipe_ratings.values(), dtype=np.int64))
        
        if self.use_features == 'rich':
            recipe_info = self.dataLoader.get_recipe_info(recipe_id)
            calories = recipe_info['calories'] if not recipe_info['calories'] is None else 0
            feats = {
                'user_id': user_id,
                'recipe_id': recipe_id,
                'avg_user_rating': avg_user_rating,
                'avg_recipe_rating': avg_recipe_rating,
                'calories': calories
            }

            for category in recipe_info["categories"]:
                feats["cat_{}".format(category)] = 1
            for ingredient in recipe_info["ingredients"]["full list"]:
                ing_name = ingredient["key ingredient"]
                quantity = ingredient["quantity"]
                feats["ing_{}".format(ing_name)] = quantity if not quantity is None else 1

        elif self.use_features == 'ratings':
            feats = {
                'user_id': user_id,
                'recipe_id': recipe_id,
                'avg_user_rating': avg_user_rating,
                'avg_recipe_rating': avg_recipe_rating,
            }        
            for other_recipe_id, rating in user_ratings.items():
                feats[str((user_id, other_recipe_id))] = rating
            for other_user_id, rating in recipe_ratings.items():
                feats[str((other_user_id, recipe_id))] = rating
        else:
             raise ValueError("Unrecognzied feature set: {}".format(self.use_features))   
                
        return feats
    
    def fit(self, X, y):
        """
        X: list of (user_id, recipe_id) tuple
        y: np.array user rating
        """
        feats = self.extract_features(X)
        feats = self.vec.fit_transform(feats)
        return self.regressor.fit(feats, y)
        
    def predict(self, X):
        """
        X: list of (user_id, recipe_id) tuple
        """
        feats = self.extract_features(X)
        feats = self.vec.transform(feats)
        return self.regressor.predict(feats)
    
    def get_params(self, deep=False):
        return {
            'dataLoader': self.dataLoader,
            'user_holdout': self.user_holdout,
            'recipe_holdout': self.recipe_holdout,
        }

In [51]:
class RandomForestEstimator:
    def __init__(self, dataLoader, recipe_holdout, user_holdout):
        self.dataLoader = dataLoader
        self.recipe_holdout = recipe_holdout
        self.user_holdout = user_holdout
        self.classifier = RandomForestClassifier(n_estimators=100)
        self.vec = DictVectorizer()
    
    def extract_features(self, X):
        feats = [self.get_feature_dict(user_id, recipe_id) for user_id, recipe_id in X]
        return feats
    
    def get_feature_dict(self, user_id, recipe_id):
        user_ratings = self.dataLoader.get_user_ratings(user_id, self.user_holdout)
        avg_user_rating = np.mean(np.fromiter(user_ratings.values(), dtype=np.int64))
        
        recipe_ratings =  self.dataLoader.get_recipe_ratings(
            recipe_id, self.recipe_holdout)
        avg_recipe_rating = np.mean(np.fromiter(recipe_ratings.values(), dtype=np.int64))

        feats = {
            'user_id': user_id,
            'recipe_id': recipe_id,
            'avg_user_rating': avg_user_rating,
            'avg_recipe_rating': avg_recipe_rating,
        }
        
        for other_recipe_id, rating in user_ratings.items():
            feats[str((user_id, other_recipe_id))] = rating
        for other_user_id, rating in recipe_ratings.items():
            feats[str((other_user_id, recipe_id))] = rating
        
        return feats
        
    def fit(self, X, y):
        """
        X: list of (user_id, recipe_id) tuple
        y: np.array user rating
        """
        feats = self.extract_features(X)
        feats =  self.vec.fit_transform(feats)
        return self.classifier.fit(feats, y)
        
    def predict(self, X):
        """
        X: list of (user_id, recipe_id) tuple
        """
        feats = self.extract_features(X)
        feats = self.vec.transform(feats)
        return self.classifier.predict(feats)
    
    def get_params(self, deep=False):
        return {
            'dataLoader': self.dataLoader,
            'user_holdout': self.user_holdout,
            'recipe_holdout': self.recipe_holdout,
        }

In [103]:
# Initialize estimators
# recipeMeanEstimator = RecipeMeanEstimator(dataLoader, recipe_holdout)
# recipeMeanEstimator.fit(holdout_X, holdout_Y)

# userMeanEstimator = UserMeanEstimator(dataLoader, user_holdout)
# userMeanEstimator.fit(holdout_X, holdout_Y)

collabFilterEstimator = CollaborativeFilteringEstimator(dataLoader, recipe_holdout, user_holdout)

# logitEstimator = LogisticEstimator(dataLoader, recipe_holdout, user_holdout)
# logitEstimator.fit(holdout_X, holdout_Y)

# randomForestEstimator = RandomForestEstimator(dataLoader, recipe_holdout, user_holdout)
# randomForestEstimator.fit(holdout_X, holdout_Y)

# tunedMeanEstimator = TunedMeanEstimator(dataLoader, recipe_holdout, user_holdout)
# tunedMeanEstimator.fit(holdout_X, holdout_Y)

In [104]:
# Perform 5-fold cross-validation on the training dataset
# print("Recipe Mean Estimator Cross-Val F1-Macro Score",
#       np.mean(cross_val_score(recipeMeanEstimator, holdout_X, holdout_Y, cv=5, scoring='f1_macro')))

# print("User Mean Estimator Cross-Val F1-Macro Score", 
#       np.mean(cross_val_score(userMeanEstimator, holdout_X, holdout_Y, cv=5, scoring='f1_macro')))
 
# print("Collab Filter Estimator Cross-Val F1-Macro Score",
#       np.mean(cross_val_score(collabFilterEstimator, holdout_X, holdout_Y, cv=5, scoring='f1_macro')))

# print("Logistic Regression Cross-Val F1-Macro Score",
#      np.mean(cross_val_score(logitEstimator, holdout_X, holdout_Y, cv=5, scoring='f1_macro')))

# print("Random Forest Cross-Val F1-Macro Score",
#       np.mean(cross_val_score(randomForestEstimator, holdout_X, holdout_Y, cv=5, scoring='f1_macro')))

# print("Tuned Mean Cross-Val F1-Macro Score",
#         np.mean(cross_val_score(tunedMeanEstimator, holdout_X, holdout_Y, cv=5, scoring='f1_macro')))

C:\Users\gblak\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1143: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


Collab Filter Estimator Cross-Val F1-Macro Score 0.2247208869168397


In [103]:
logitEstimator = LogisticEstimator(dataLoader, recipe_holdout, user_holdout)
classifier= logitEstimator.fit(holdout_X, holdout_Y)
coef = classifier.coef_

In [68]:
# Perform feature elimination on logistic regression
## WARNING: Takes a long time
logitEstimator = LogisticEstimator(dataLoader, recipe_holdout, user_holdout, features='ratings')
logitEstimator.fit(holdout_X, holdout_Y)
# TODO: Try reducing step
rfecv = RFECV(estimator=logitEstimator.regressor, step=100, scoring='f1_macro', verbose=1)
rfecv.fit(logitEstimator.vec.transform(logitEstimator.extract_features(holdout_X)), holdout_Y)
# logitEstimator.vec.transform(logitEstimator.extract_features(holdout_X))

with open("models/rfecv_trained_ratings.pkl", 'wb') as outfile:
    pickle.dump(rfecv, outfile)


C:\Users\gblak\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:2053: FutureWarning: You should specify a value for 'cv' instead of relying on the default value. The default value will change from 3 to 5 in version 0.22.
  warnings.warn(CV_WARNING, FutureWarning)
C:\Users\gblak\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:652: Warning: The least populated class in y has only 1 members, which is too few. The minimum number of members in any class cannot be less than n_splits=3.
  % (min_groups, self.n_splits)), Warning)
C:\Users\gblak\Anaconda3\lib\site-packages\sklearn\linear_model\logistic.py:433: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
C:\Users\gblak\Anaconda3\lib\site-packages\sklearn\linear_model\logistic.py:460: FutureWarning: Default multi_class will be changed to 'auto' in 0.22. Specify the multi_class option to silence this warning.
  "this warning.", FutureWarning

Fitting estimator with 137285 features.


C:\Users\gblak\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1143: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
C:\Users\gblak\Anaconda3\lib\site-packages\sklearn\linear_model\logistic.py:433: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
C:\Users\gblak\Anaconda3\lib\site-packages\sklearn\linear_model\logistic.py:460: FutureWarning: Default multi_class will be changed to 'auto' in 0.22. Specify the multi_class option to silence this warning.
  "this warning.", FutureWarning)


Fitting estimator with 137185 features.


C:\Users\gblak\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1143: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
C:\Users\gblak\Anaconda3\lib\site-packages\sklearn\linear_model\logistic.py:433: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
C:\Users\gblak\Anaconda3\lib\site-packages\sklearn\linear_model\logistic.py:460: FutureWarning: Default multi_class will be changed to 'auto' in 0.22. Specify the multi_class option to silence this warning.
  "this warning.", FutureWarning)


...

C:\Users\gblak\Anaconda3\lib\site-packages\sklearn\svm\base.py:931: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)
C:\Users\gblak\Anaconda3\lib\site-packages\sklearn\linear_model\logistic.py:433: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
C:\Users\gblak\Anaconda3\lib\site-packages\sklearn\linear_model\logistic.py:460: FutureWarning: Default multi_class will be changed to 'auto' in 0.22. Specify the multi_class option to silence this warning.
  "this warning.", FutureWarning)


Fitting estimator with 285 features.


C:\Users\gblak\Anaconda3\lib\site-packages\sklearn\svm\base.py:931: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)
C:\Users\gblak\Anaconda3\lib\site-packages\sklearn\linear_model\logistic.py:433: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
C:\Users\gblak\Anaconda3\lib\site-packages\sklearn\linear_model\logistic.py:460: FutureWarning: Default multi_class will be changed to 'auto' in 0.22. Specify the multi_class option to silence this warning.
  "this warning.", FutureWarning)


Fitting estimator with 185 features.


C:\Users\gblak\Anaconda3\lib\site-packages\sklearn\svm\base.py:931: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)
C:\Users\gblak\Anaconda3\lib\site-packages\sklearn\linear_model\logistic.py:433: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
C:\Users\gblak\Anaconda3\lib\site-packages\sklearn\linear_model\logistic.py:460: FutureWarning: Default multi_class will be changed to 'auto' in 0.22. Specify the multi_class option to silence this warning.
  "this warning.", FutureWarning)
C:\Users\gblak\Anaconda3\lib\site-packages\sklearn\svm\base.py:931: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)


In [105]:
# coef[0]
# classifier.intercept_
# feat_names = np.array(logitEstimator.vec.get_feature_names())



# for idx, cat in enumerate(classifier.classes_):
#     print("Category: {}".format(cat))
#     sorted_index = np.argsort(np.abs(coef[idx]))[::-1]
#     res = zip(feat_names[sorted_index[:10]], coef[idx][sorted_index[:10]])
    
#     for i1, i2 in res:
#         print("{}: {}".format(i1, i2))
        
#     print("")
    
#     print(feat_names[sorted_index[:10]])
#     print(coef[idx][sorted_index[:10]])

# dataLoader.recipe_to_raters_train
# logitEstimator = LogisticEstimator(dataLoader, recipe_holdout, user_holdout, features='ratings')
# logitEstimator.fit(holdout_X, holdout_Y)
# pred_logit = logitEstimator.predict(test_holdout_X)
# rfecv.n_features_
# pred_collab = collabFilterEstimator.predict(test_holdout_X)
# np.clip(pred_collab[100:200], 1.0, 5.0)
# np.min(pred_collab)
# np.max(collabFilterEstimator.similarity, axis=1)
# for i in range(32):
#     start = i * 100
#     end = start + 100
#     print(collabFilterEstimator.similarity[2][start:end])


Collab Filter Test:
F1 Weighted: 0.6002978112204793
F1 Macro 0.3377295380845524
Lower-3 Recall: 0.1432806324110672


In [13]:
def print_scores(name, true_Y, pred_Y):
    print("\n{}:\nF1 Weighted: {}\nF1 Macro {}\nLower-3 Recall: {}".format(
        name,
        f1_score(true_Y, pred_Y, average='weighted'),
        f1_score(true_Y, pred_Y, average='macro'),
        np.mean(recall_score(true_Y, pred_Y, average=None)[:3])))

In [108]:
# Test performance on Ratings Only dataset
ratings = pd.read_csv("data/all_recipe_small_clean.csv")
dataLoader = DataLoader.DataLoader(ratings, None)
user_holdout, recipe_holdout, holdout = dataLoader.get_holdout_data()
holdout_X = [t[:2] for t in holdout]
holdout_Y = np.array([t[2] for t in holdout])

test_user_holdout, test_recipe_holdout, test_holdout = dataLoader.get_holdout_data(split='test')
test_holdout_X = [t[:2] for t in test_holdout]
test_holdout_Y = np.array([t[2] for t in test_holdout])

print("Final Test Scores - Ratings Only")
with open("models/rfecv_trained_ratings.pkl", "rb") as infile:
    rfecv_ratings = pickle.load(infile)

collabFilterEstimator = CollaborativeFilteringEstimator(dataLoader, test_recipe_holdout, test_user_holdout, split='test')
pred_collab = collabFilterEstimator.predict(test_holdout_X)
print_scores("Collab Filter Test", test_holdout_Y, pred_collab)

logitEstimator = LogisticEstimator(dataLoader, recipe_holdout, user_holdout, features='ratings')
logitEstimator.fit(holdout_X, holdout_Y)
pred_logit = logitEstimator.predict(test_holdout_X)
print_scores("Logit Test", test_holdout_Y, pred_logit)
    
pred_rfecv = rfecv_ratings.predict(logitEstimator.vec.transform(logitEstimator.extract_features(test_holdout_X)))
print_scores("RFECV Logit Test", test_holdout_Y, pred_rfecv)

recipeMeanEstimator = RecipeMeanEstimator(dataLoader, recipe_holdout)
recipeMeanEstimator.fit(holdout_X, holdout_Y)
pred_recipe = recipeMeanEstimator.predict(test_holdout_X)
print_scores("Recipe Mean Test", test_holdout_Y, pred_recipe)
    
userMeanEstimator = UserMeanEstimator(dataLoader, user_holdout)
pred_ume = userMeanEstimator.predict(test_holdout_X)
print_scores("User Mean Test", test_holdout_Y, pred_ume)


Final Test Scores - Ratings Only

Collab Filter Test:
F1 Weighted: 0.5157713802823575
F1 Macro 0.2704265747169844
Lower-3 Recall: 0.09241483154526632

Logit Test:
F1 Weighted: 0.5192800149018194
F1 Macro 0.22283651929030346
Lower-3 Recall: 0.03613777526821005

RFECV Logit Test:
F1 Weighted: 0.527307411018668
F1 Macro 0.2270818201683789
Lower-3 Recall: 0.08375682288725768

Recipe Mean Test:
F1 Weighted: 0.47113869204426695
F1 Macro 0.1973644065159375
Lower-3 Recall: 0.004329004329004329

User Mean Test:
F1 Weighted: 0.5951466315718383
F1 Macro 0.24695803338487898
Lower-3 Recall: 0.06601731601731602


In [109]:
# Test performance on  Full Recipe dataset
ratings = pd.read_csv("data/all_ratings.csv")
with open("data/all_recipes.pkl", "rb") as infile:
    recipes = pickle.load(infile) 

dataLoader = DataLoader.DataLoader(ratings, recipes)
user_holdout, recipe_holdout, holdout = dataLoader.get_holdout_data()
holdout_X = [t[:2] for t in holdout]
holdout_Y = np.array([t[2] for t in holdout])

test_user_holdout, test_recipe_holdout, test_holdout = dataLoader.get_holdout_data(split='test')
test_holdout_X = [t[:2] for t in test_holdout]
test_holdout_Y = np.array([t[2] for t in test_holdout])

print("Final Test Scores - Full Recipe")
with open("models/rfcev_trained.pkl", "rb") as infile:
    rfecv = pickle.load(infile)

collabFilterEstimator = CollaborativeFilteringEstimator(dataLoader, test_recipe_holdout, test_user_holdout, split='test')
pred_collab = collabFilterEstimator.predict(test_holdout_X)
print_scores("Collab Filter Test", test_holdout_Y, pred_collab)

logitEstimator = LogisticEstimator(dataLoader, recipe_holdout, user_holdout)
logitEstimator.fit(holdout_X, holdout_Y)
pred_logit = logitEstimator.predict(test_holdout_X)
print_scores("Logit Test", test_holdout_Y, pred_logit)
    
pred_rfecv = rfecv.predict(logitEstimator.vec.transform(logitEstimator.extract_features(test_holdout_X)))
print_scores("RFECV Logit Test", test_holdout_Y, pred_rfecv)

recipeMeanEstimator = RecipeMeanEstimator(dataLoader, recipe_holdout)
recipeMeanEstimator.fit(holdout_X, holdout_Y)
pred_recipe = recipeMeanEstimator.predict(test_holdout_X)
print_scores("Recipe Mean Test", test_holdout_Y, pred_recipe)
    
userMeanEstimator = UserMeanEstimator(dataLoader, user_holdout)
pred_ume = userMeanEstimator.predict(test_holdout_X)
print_scores("User Mean Test", test_holdout_Y, pred_ume)


Final Test Scores - Full Recipe

Collab Filter Test:
F1 Weighted: 0.4467865035561388
F1 Macro 0.22953494649392284
Lower-3 Recall: 0.04555984555984557

Logit Test:
F1 Weighted: 0.5001490274099712
F1 Macro 0.25215789410257383
Lower-3 Recall: 0.11012441012441014

RFECV Logit Test:
F1 Weighted: 0.505175534713902
F1 Macro 0.26957625051770595
Lower-3 Recall: 0.15507293007293008

Recipe Mean Test:
F1 Weighted: 0.3435928702677624
F1 Macro 0.1869809461700083
Lower-3 Recall: 0.028056628056628053

User Mean Test:
F1 Weighted: 0.5750846921504087
F1 Macro 0.2971863887012698
Lower-3 Recall: 0.06658086658086658


In [21]:
logitEstimator = LogisticEstimator(dataLoader, recipe_holdout, user_holdout, features='ratings')
logitEstimator.fit(holdout_X, holdout_Y)
pred_logit = logitEstimator.predict(test_holdout_X)
print_scores("Logit Test", test_holdout_Y, pred_logit)
# print_scores("All 5", test_holdout_Y, [5.0] * len(test_holdout_Y))


Logit Test:
F1 Weighted: 0.44947745709195436
F1 Macro 0.1817664298126756
Lower-3 Recall: 0.015529815529815529
